# Catchment delineation
In this Notebook, using a DEM we aim to delineate the area—referred to as a catchment, watershed, or basin—that drains or contributes water to a specific point known as the catchment outlet. This will be our area of study from now on.

The steps in catchment delineation typically involve:

1. **Topographical Analysis**: Using topographic maps or digital elevation models (DEMs) to identify natural drainage paths.
2. **Flow Direction and Accumulation**: Determining the direction of water flow across the landscape by analyzing the slope and elevation of each point in the DEM.
3. **Outlet Identification**: Selecting an outlet or "pour point" where water exits the catchment.
4. **Boundary Definition**: Tracing the ridgeline or divide around the pour point to outline the catchment area.

Catchment delineation can be done manually using maps or more commonly through GIS (Geographic Information Systems) software, which automates the process by processing DEMs.

<left><img src="images/catchment.png" width="800px">

## Import the necessary libraries and iMPACT-tools
These tools will let us delineate and plot the catchment and save the results.
##### Import tools

In [1]:
import os
import numpy as np
from numba import njit
from ipywidgets import fixed, interactive, Dropdown
import pandas as pd
import matplotlib.pyplot as plt
# Import the necessary iMPACTools (you can find these tools in the Python files stored in the */iMPACtools* folder)
os.chdir('..') # change the current working directory to the parent directory
from iMPACTools.catchment_delineation import plot_catchment_delineation
from iMPACTools.file_IO import open_raster, save_as_raster
from iMPACTools.plot_dem import plot3d_dem, plot3d_dem_plotly
from iMPACTools.dem_analysis import slope_gradient
from iMPACTools.flow_accumulation import flow_accumulation_D8, flow_accumulation_Dinf

## Choose the case study

In [2]:
# Get list of case studies (folders in the Case_studies directory)
case_study = Dropdown(options=os.listdir('Case_studies'),description='Case Study:')
display(case_study)

Dropdown(description='Case Study:', options=('Montefrio', 'SantaCruz'), value='Montefrio')

### Load the DEM and compute the flow direction and flow accumulation of the area of study
<left><img src="images/open_raster.png" width="200px">
##### Open the DEM file and calculate the flow direction and flow accumulation maps

In [16]:
# Open the Digital Elevation Model (DEM) raster file
dem, metadata = open_raster(f'Case_studies/{case_study.value}/topo/','dem_fill.tif')
dem_resol= metadata['transform'][0]
# Open the slope raster file
slope, metadata = open_raster(f'Case_studies/{case_study.value}/topo/','slope.tif')
# Run the function
flow_dir_D8,flow_acc_D8,_, _, _, _, _, _ = flow_accumulation_D8(dem,slope)

### Function for catchment delineation
In simple terms, the function `catchment_delineation` helps you understand how water flows over a landscape (DEM) and shows you the exact area that will contribute water to a particular outlet.
1. **Define outlet**: first we define a specific point on the map where the water flows out, called the catchment "outlet." 
2. **Trace the water flow**: beginning at the outlet, the function looks at all the nearby areas to check which ones flow towards the outlet, or in other words, it looks for cells of the DEM that are connected to the outlet. 
3. **Mark the catchment cells**: when the function finds a cell where water flows towards the outlet, it marks that cell as part of the catchment. 
4. **Keep Exploring**: it then continues to check the neighboring cells.
5. **Delineation of the catchment area**: once all cells have been checked, the function gives you a final map. This map shows you the entire catchment area – all the land that will drain water into the outlet.

##### Python implementation of the `catchment_delineation` function

In [17]:
@njit
def catchment_delineation(dem,flow_direction, outlet_row, outlet_col):
    """
    Delineates the catchment area based on flow direction and the location of the catchment outlet.

    Args:
        dem (numpy.ndarray): 2D array of the digital elevation model.
        flow_direction (numpy.ndarray): 2D array representing flow direction values.
        outlet_row (int): Row index of the catchment outlet cell.
        outlet_col (int): Column index of the catchment outlet cell.

    Returns:
        catchment_mask (numpy.ndarray): Binary mask indicating the delineated catchment area.
        catchment_dem (numpy.ndarray: DEM of the delineated catchment area
    """
    
    ######################
    ### Initialization ###
    ######################
    # Initialize a mask (boolean array) to track visited cells during reverse tracing
    visited = np.zeros_like(flow_direction, dtype=np.bool_)

    # Initialize the catchment mask (boolean array) to represent the catchment area
    catchment_mask = np.zeros_like(flow_direction, dtype=np.bool_)*np.nan

    #######################
    ### Reverse tracing ###
    #######################   
    # Start reverse tracing from the outlet cell and explores neighboring cells recursively
    
    # Create the variable stack to keep track of the cells that need to be explored during the reverse tracing process.
    stack = [(outlet_row, outlet_col)] # Add the first catchment cell (outlet) to the stack
    
    while stack: # It continues this process while there are cells (in stack) to explore.
        
        current_row, current_col = stack.pop() # return and remove the last item from the stack

        # Check if the current cell has been visited
        if visited[current_row, current_col]:
            continue

        # Mark the current cell as visited
        visited[current_row, current_col] = True

        # Mark the current cell as part of the catchment
        catchment_mask[current_row, current_col] = 1
        
        ##########################
        ### Neighbor Selection ###
        ##########################

        # Define a 3x3 array to represent the directions of the valid neighboring cells (connected to the current cell)
        neighbours_dir = np.array([(2,    4,  8),
                                   (1,    0, 16),
                                   (128, 64, 32)], dtype=np.int32)

        # Iterate over neighboring cells in a 3x3 grid centered around the current cell
        
        neighboring_cells = [] # Initialize the variable to add valid neighboring cells
        
        for dr in range(-1, 2): # change in the row index (-1: move up, 0: stay, 1: move down)
            for dc in range(-1, 2): # change in the column index (-1: move left, 0: stay, 1: move right)
                
                if dr == 0 and dc == 0: # exclude the current cell itself
                    continue
                    
                new_row, new_col = current_row + dr, current_col + dc
                
                # Determine valid neighboring cells: check if each neighboring cell satisfies certain conditions
                if (0 <= new_row < flow_direction.shape[0] and # It's within the bounds of the array.
                    0 <= new_col < flow_direction.shape[1] and # It's within the bounds of the array.
                    not visited[new_row, new_col] and # It hasn't been visited yet.
                    flow_direction[new_row, new_col] == neighbours_dir[dr+1, dc+1]): # Its flow direction matches neighbours_dir.         
                    
                    neighboring_cells.append((new_row, new_col)) # Valid neighboring cells are added
        
        #############################
        ### Recursive Exploration ###
        #############################
        # Add all the valid neighboring cells to the stack for further exploration
        stack.extend(neighboring_cells)
        
    catchment_dem = dem*catchment_mask

    # Return the catchment_mask, a boolean array indicating the delineated catchment area
    return catchment_mask,catchment_dem

### Interactive plotting function for catchment delineation
In this section, we provide an interactive tool to visualize the catchment delineation process. This interactive widget allows you to select the catchment outlet using a slider. By adjusting this slider, you can see how the catchment area changes based on the outlet's position.

<left><img src="images/catchment_delineation.png" width="400px">

##### Interactive `catchment_delineation`: using the slider select the catchment outlet

In [18]:
# Interactive plot with widgets (sliders) for selecting the catchment outlet
iplot = interactive(plot_catchment_delineation,dem = fixed(dem), fd = fixed(flow_dir_D8), fa = fixed(flow_acc_D8),outlet = (1,400))
display(iplot)

interactive(children=(IntSlider(value=1, description='outlet', max=400, min=1), Output()), _dom_classes=('widg…

### Run the function to compute the slope gradient of the *delineated catchment*
##### Calculate the slope gradient of the DEM

In [19]:
catchment_mask,catchment_dem = iplot.result
slope = slope_gradient(catchment_dem, dem_resol)
# Plot the 3D DEM with slope gradients
plot3d_dem_plotly(dem,slope,'slope gradient')

### Run the function to compute the slope, flow accumulation, flow direction and flow routing for the delineated catchment
Here we use the D8 method
##### Run the `flow_accumulation_D8` function and plot the results

In [20]:
flow_dir_D8,flow_acc_D8,flow_rout_up_row_D8, flow_rout_up_col_D8, flow_rout_down_row_D8, flow_rout_down_col_D8, flow_rout_contrib_D8, flow_rout_slope_D8 = flow_accumulation_D8(catchment_dem,slope)
plot3d_dem_plotly(catchment_dem,flow_acc_D8,'flow accumulation - D8')

##### Run the `flow_accumulation_Dinf` function  and plot the results

In [21]:
flow_acc_Dinf,flow_rout_up_row_Dinf,flow_rout_up_col_Dinf,flow_rout_down_row_Dinf, flow_rout_down_col_Dinf, flow_rout_contrib_Dinf, flow_rout_slope_Dinf = flow_accumulation_Dinf(catchment_dem)
plot3d_dem_plotly(catchment_dem,flow_acc_Dinf,'flow accumulation - Dinf')

### Interactive definition of the stream/gully network

In [13]:
def plot_stream_network(method, threshold):
    """
    Plots the stream network over a DEM and flow accumulation map based on the selected method and threshold.

    Parameters:
    - method (str): The flow accumulation method, either 'D8' or 'Dinf'.
    - threshold (int): The flow accumulation threshold to define the stream network.
    """

    # Select the appropriate flow accumulation data based on the method
    if method == 'D8':
        flow_acc = flow_acc_D8  # Flow accumulation using the D8 method
    elif method == 'Dinf':
        flow_acc = flow_acc_Dinf  # Flow accumulation using the D-Infinity method

    # Create a boolean mask where flow accumulation is below the threshold
    stream_network_mask = flow_acc <= threshold  

    # Mask the DEM and flow accumulation data using the stream network mask
    masked_dem = np.where(stream_network_mask, dem, np.nan)  # Hide non-stream areas in DEM
    masked_flow_acc = np.where(stream_network_mask, flow_acc, np.nan)  # Hide non-stream areas in flow accumulation

    # Extract grid resolution from DEM metadata
    grid_resol = metadata['transform'][0]  

    # Create a figure with two subplots (DEM + flow accumulation)
    fig, ax = plt.subplots(1, 2, figsize=(16, 5))  

    # Plot the DEM with the stream network overlay
    ax[0].imshow(masked_dem, cmap='terrain')  
    ax[0].set_title(f'DEM & Stream network (Method: {method} - Threshold: {threshold} grid cells)')

    # Plot the flow accumulation with the stream network overlay
    im = ax[1].imshow(masked_flow_acc, cmap='coolwarm')  
    ax[1].set_title(f'Flow acc ({method}) & Stream Network (threshold = {threshold * grid_resol**2 / 10000:.1f} ha)')

    # Add a color bar to indicate flow accumulation intensity
    plt.colorbar(im)

    # Display the figure
    plt.show()   

# Create an interactive widget to adjust the method and threshold dynamically
interactive(plot_stream_network, method=['D8', 'Dinf'], threshold=(0, 2000))

interactive(children=(Dropdown(description='method', options=('D8', 'Dinf'), value='D8'), IntSlider(value=1000…

#### Now define the threshold
Areas where the flow accumulation is above the threshold are set to NaN, effectively masking them out. This helps visualize only the stream network.

In [14]:
# Define the flow accumulation threshold for stream network extraction
threshold = 1000  

# Apply threshold to the D8 flow accumulation grid
# Areas where flow accumulation is greater than the threshold are masked (set to NaN)
stream_mask_D8 = np.where(flow_acc_D8 <= threshold, flow_acc_D8*0, np.nan)  

# Apply the same thresholding method to the Dinf flow accumulation grid
stream_mask_Dinf = np.where(flow_acc_Dinf <= threshold, flow_acc_Dinf*0, np.nan) 

### Save the DEM, flow accumulation and flow direction maps of the delineated catchment as a raster file and the flow routing arrays as csv files
<left><img src="images/save_raster.png" width="200px">
##### Save the results

In [15]:
# Save the DEM as raster (TIFF) files
save_as_raster(f'Case_studies/{case_study.value}/topo/','dem_catchment.tif',catchment_dem,metadata)
# Save the slope, flow direction, and flow accumulation maps as raster (TIFF) files
save_as_raster(f'Case_studies/{case_study.value}/topo/','slope.tif', slope, metadata)
save_as_raster(f'Case_studies/{case_study.value}/flow/','flow_dir_D8.tif', flow_dir_D8, metadata)
save_as_raster(f'Case_studies/{case_study.value}/flow/','flow_acc_D8.tif', flow_acc_D8, metadata)
save_as_raster(f'Case_studies/{case_study.value}/flow/','flow_acc_Dinf.tif', flow_acc_Dinf, metadata)
save_as_raster(f'Case_studies/{case_study.value}/flow/','stream_mask_D8.tif', stream_mask_D8, metadata)
save_as_raster(f'Case_studies/{case_study.value}/flow/','stream_mask_Dinf.tif', stream_mask_Dinf, metadata)

# Save the D8 flow routing data to a CSV file
df_D8 = pd.DataFrame() 
df_D8['upstream_row'] = flow_rout_up_row_D8   # Row indices of upstream cells for D8 method
df_D8['upstream_col'] = flow_rout_up_col_D8   # Column indices of upstream cells for D8 method
df_D8['downstream_row'] = flow_rout_down_row_D8  # Row indices of downstream cells for D8 method
df_D8['downstream_col'] = flow_rout_down_col_D8  # Column indices of downstream cells for D8 method
df_D8['contribution'] = flow_rout_contrib_D8   # Flow contributions from upstream to downstream cells
df_D8['slope'] = flow_rout_slope_D8 + [0]   # Slope values along the flow paths for D8 (added [0] to match length)
df_D8.to_csv(f'Case_studies/{case_study.value}/flow/flow_routing_D8.csv', index=False)  # Export the DataFrame to a CSV file

# Save the D-infinity flow routing data to a CSV file
df_Dinf = pd.DataFrame()
df_Dinf['upstream_row'] = flow_rout_up_row_Dinf  # Row indices of upstream cells for D-infinity method
df_Dinf['upstream_col'] = flow_rout_up_col_Dinf  # Column indices of upstream cells for D-infinity method
df_Dinf['downstream_row'] = flow_rout_down_row_Dinf  # Row indices of downstream cells for D-infinity method
df_Dinf['downstream_col'] = flow_rout_down_col_Dinf  # Column indices of downstream cells for D-infinity method
df_Dinf['contribution'] = flow_rout_contrib_Dinf  # Flow contributions from upstream to downstream cells
df_Dinf['slope'] = flow_rout_slope_Dinf  # Slope values along the flow paths for D-infinity method
df_Dinf.to_csv(f'Case_studies/{case_study.value}/flow/flow_routing_Dinf.csv', index=False)  # Export the DataFrame to a CSV file